In [1]:
import warnings
warnings.filterwarnings("ignore")

import streamlit as st
from streamlit_folium import folium_static
from streamlit_echarts import st_pyecharts

from bs4 import BeautifulSoup
import requests
import re
import urllib.request
import plotly.graph_objects as go

import pandas as pd
import numpy as np
import plotly.express as px

import json

import folium

import pyecharts.options as opts

from pyecharts.charts import Calendar
from pyecharts.charts import Bar, Line, Scatter, EffectScatter, Timeline
from pyecharts import options as opts
from pyecharts.commons.utils import JsCode
from pyecharts.globals import ThemeType
from pyecharts.components import Table
from pyecharts.options import ComponentTitleOpts

import datetime

In [2]:
def json_to_df(url, lista_datos_acumulados):
    """Función para extraer datos por municipio por provincia.
    Esta función habrá que ejecutarla 8 veces (1 vez por provincia).

    Parameters
    ----------
    url : string
        _URL del json de cada provincia con los datos municipales.
    lista_datos_acumulados : list
        lista con los datos acumulados que salen en la tabla de la página de la junta.

    Returns
    -------
    DataFrame
        Dataframe con los datos de la provincia con los municipios como índice.
    """
    payload = {}
    headers = {}
    
    data = []
    response = requests.request("GET", url, headers=headers, data = payload,verify=False)
    df = response.json()
    
    columnas = [x['des'] for x in df['measures']]
    indice = [x[0]['des'] for x in df['data']]
    
    for i in range(len(df['data'])):
        aux = [x['val'] for x in df['data'][i] if 'val' in x.keys()]
        tup = tuple(aux)
        data.append(tup)
    data = pd.DataFrame(data,columns=columnas)
    data['indice'] = indice
    data = data[-data['indice'].isin(lista_datos_acumulados)].reset_index(drop=True)
    data = data.set_index(['indice'])
    return data.applymap(lambda x : float(x) if x!='' else np.nan)
    return data

In [3]:
url = "https://www.juntadeandalucia.es/institutodeestadisticaycartografia/intranet/admin/rest/v1.0/consulta/38665"
lista_acumulados = ['Almería','Almería (distrito)','Levante-Alto Almanzora','Poniente de Almería']
almeria_df = json_to_df(url,lista_acumulados)

In [8]:
almeria_df = almeria_df.fillna(0)

In [9]:
## Limpieza de la tabla
almeria_df.reset_index(inplace=True)
almeria_df['indice2'] = [re.sub(r'(.*) \((.*)\)',r'\2 \1',x) if '(' in x else x for x in almeria_df['indice']]
almeria_df['indice2'] = [re.sub(r'capital (.*)',r'\1',x) if 'capital' in x else x for x in almeria_df['indice2']]

In [11]:
with open('Geojson/Almería.geojson',encoding="utf-8") as f:
        geo = json.load(f, encoding="utf-8")

In [12]:
for x in range(len(geo['features'])):
    geo['features'][x]['properties']['Total_confirmados'] = almeria_df[almeria_df.indice2 == geo['features'][x]['properties']['NAMEUNIT']]['Total confirmados'].tolist()[0]
    geo['features'][x]['properties']['Curados'] = almeria_df[almeria_df.indice2 == geo['features'][x]['properties']['NAMEUNIT']]['Curados'].tolist()[0]
    geo['features'][x]['properties']['Fallecidos'] = almeria_df[almeria_df.indice2 == geo['features'][x]['properties']['NAMEUNIT']]['Fallecidos'].tolist()[0]

In [30]:
m = folium.Map(location=[37.3, -2.5], zoom_start=9)

## Mediante folium realizamos el mapa

cloropeth = folium.Choropleth(
    geo_data=geo,
    name='choropleth',
    data=almeria_df,
    columns=['indice2','Total confirmados'],
    key_on='feature.properties.NAMEUNIT',
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2).add_to(m)

# add labels indicating the name of the community
style_function = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.1, 
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.50, 
                                'weight': 0.1}

NIL = folium.features.GeoJson(
    geo,
    style_function=style_function, 
    control=False,
    highlight_function=highlight_function, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['NAMEUNIT','Total_confirmados','Curados','Fallecidos'],
        aliases=['Municipio','Confirmados totales','Curados','Fallecidos'],
        style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
m.add_child(NIL)
m.keep_in_front(NIL)
folium.LayerControl().add_to(m)
m